In [83]:
# issue fixed with pytube: https://github.com/pytube/pytube/issues/1408
import pytube
from pytube.exceptions import PytubeError
import http.client
from googleapiclient.discovery import build
import pandas as pd
import sys
from constants import YOUTUBE_API_KEY
from data_mining import data_mining_source
import os
from random import sample
import moviepy
import pretty_midi
import numpy as np
import copy

In [84]:
sys.path.insert(0, '/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn')
sys.path.insert(0, '/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/data_mining')

In [85]:
eval_sources = pd.read_csv('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/eval_sources.csv')
eval_sources

name                                               link  \
0           Pragya Gaur  https://www.youtube.com/channel/UCD9qgumkKNOz9...   
1          The Theorist              https://www.youtube.com/c/TheTheorist   
2  zzz - Anime on Piano  https://www.youtube.com/channel/UCXbCo1dYKNceo...   
3             AnimeMidi  https://www.youtube.com/channel/UC9nPjOh-1V4pn...   
4        Marioverehrer2           https://www.youtube.com/c/Marioverehrer2   
5          Cosmic PIANO              https://www.youtube.com/c/cosmicpiano   

             genre  
0           Indian  
1          Hip-Hop  
2            Anime  
3            K-pop  
4       Video Game  
5  EDM-Anime-Movie

In [86]:
url_list = eval_sources['link'].values.tolist()
url_list

['https://www.youtube.com/channel/UCD9qgumkKNOz9KYVLOSVvQw',
 'https://www.youtube.com/c/TheTheorist',
 'https://www.youtube.com/channel/UCXbCo1dYKNceoxUC7rKMjZw',
 'https://www.youtube.com/channel/UC9nPjOh-1V4pnRlZYpJeoBg',
 'https://www.youtube.com/c/Marioverehrer2',
 'https://www.youtube.com/c/cosmicpiano']

In [7]:
channel_table = data_mining_source.channel_metadata(url_list)
channel_table

ChannelID           ChannelName  \
0  UCD9qgumkKNOz9KYVLOSVvQw           Pragya Gaur   
1  UCWBKJ1RNeKTPII34pc6UyUg          The Theorist   
2  UCXbCo1dYKNceoxUC7rKMjZw  zzz - Anime on Piano   
3  UC9nPjOh-1V4pnRlZYpJeoBg             AnimeMidi   
4  UCrOaijB2OTbuH0Sc7Ifee1A         Marioverehrer   
5  UCpHGeKwKQVHaH0VPVlyhfww        Cosmic PIANO ♪   

                                           AllVideos  
0  ['https://www.youtube.com/watch?v=6x2oxlzcr4I'...  
1  ['https://www.youtube.com/watch?v=Bb1x0L59WU0'...  
2  ['https://www.youtube.com/watch?v=F1Gg6pTnD18'...  
3  ['https://www.youtube.com/watch?v=D-H28Smg4fI'...  
4  ['https://www.youtube.com/watch?v=MyJmC65H1IM'...  
5  ['https://www.youtube.com/watch?v=NMl19JxyFh0'...

## UDFs

In [87]:
def download(genre, video_urls):
    try:
        for video_url in video_urls:
            video = pytube.YouTube(video_url)
            output_path = os.path.join('dataset', genre, video.title)
            video_name = video.title.replace('/', '') + '.mp4'
            audio_name = video.title.replace('/', '') + '.mp3'

            if not os.path.isdir(output_path) and not video.length > 360:
                os.makedirs(output_path)

            if not os.path.isfile(os.path.join(output_path, audio_name)) and not video.length > 360:
                video.streams.filter(progressive=True, file_extension='mp4').order_by('resolution').asc() \
                    .first().download(filename=video_name, output_path=output_path)

                video_editor = moviepy.editor.VideoFileClip(os.path.join(output_path, video_name))
                video_editor.audio.write_audiofile(os.path.join(output_path, audio_name), logger=None)
                os.remove(os.path.join(output_path, video_name))
        print()
    except (PytubeError, http.client.IncompleteRead) as e:
        print('Error: ', e)
        return None

In [88]:
# for mt3 transcription editing
def remove_tracks(midi_data):
    # check if multi-track, if multi-track then remove the non-piano instruments
    print(f'original midi: {midi_data.instruments}')
    for instrument in midi_data.instruments:
        print(f'program: {instrument.program}')
        if instrument.program == 0:
            piano = instrument
            break
    midi_data.instruments = [piano]
    print(f'new midi: {midi_data.instruments}')

    # checking if there are notes in the midi data
    for instrument in midi_data.instruments:
        if len(instrument.notes) != 0:
            print('Has notes!')

    return midi_data

In [158]:
# for ground truth editing
def merge_tracks(midi_path, output_path):
    midi_data = pretty_midi.PrettyMIDI(midi_path)
    new_instrument = pretty_midi.Instrument(program=0, is_drum=False, name="merged")

    # Iterate through all notes in all instruments in the original MIDI data
    for instrument in midi_data.instruments:
        for note in instrument.notes:
            # Add each note to the merged instrument
            new_instrument.notes.append(note)

    midi_data.instruments = [new_instrument]

    # Write the merged MIDI data to disk
    midi_data.write(output_path)

In [90]:
# for mt3 transcription editing
def remove_silence(midi_path, output_path):
    midi_data = pretty_midi.PrettyMIDI(midi_path)

    # remove non-piano instruments
    midi_data = remove_tracks(midi_data)

    # original times
    ori_times = midi_data.get_onsets()
    print(ori_times[:10])

    # new times
    new_times = midi_data.get_onsets() - midi_data.get_onsets()[0]
    print(new_times[:10])

    # adjusting times
    midi_data.adjust_times(ori_times, new_times)

    midi_data.write(output_path)

In [144]:
# for ground truth editing
def complex_remove_silence(midi_path, output_path):
    midi_data = pretty_midi.PrettyMIDI(midi_path)

    new_instrument = pretty_midi.Instrument(program=0, is_drum=False, name="merged")
    for instrument in midi_data.instruments:
        notes_lst = instrument.notes
        leftover = []
        i = 0
        print(f'original length of track: {len(instrument.notes)}')

        while i < len(instrument.notes) - 1:
            diff = instrument.notes[i+1].start - instrument.notes[i].end

            if diff >= 5:
                print(f'index: {i}')
                # if at the end (next one is last)
                if i + 1 == len(instrument.notes) - 1:
                    leftover.append(instrument.notes[i + 1:])
                    notes_lst = notes_lst[:i]
                else:
                    leftover.append(instrument.notes[:i + 1])
                    notes_lst = notes_lst[i + 1:]
            i += 1
    print(f'leftover after removing: {leftover}')

    # original (after "trimming" gaps)
    for note in notes_lst:
        new_instrument.notes.append(note)
    midi_data.instruments = [new_instrument]
    print(f'new length of track: {len(new_instrument.notes)}')

    # original times (start)
    ori_times = midi_data.get_onsets()
    print(f'checking onsets: {midi_data.get_onsets()}')

    # new times (start)
    new_times_lst = midi_data.get_onsets() - midi_data.get_onsets()[0]

    original_times, unique_idx = np.unique(ori_times, return_index=True)
    new_times = np.asarray(new_times_lst)[unique_idx]

    # ------------------------------------------------------
    print(f'original_times: {len(original_times)}')
    print(f'new_times: {len(new_times)}')
    print('')
    # ------------------------------------------------------

    interval = []
    for instrument in midi_data.instruments:
        for note in instrument.notes:
            interval.append(note.end - note.start)


    # ------------------------------------------------------
    """print('INTERVALS')
    [print(i) for i in interval]
    print('')"""
    # ------------------------------------------------------

    # Get array of note-on locations and correct them
    note_ons = np.array([note.start for instrument in midi_data.instruments
                            for note in instrument.notes])
    adjusted_note_ons = np.interp(note_ons, original_times, new_times)

    # ------------------------------------------------------
    """print(f'note_ons: {len(note_ons)}')
    print(f'adjusted_note_ons: {len(adjusted_note_ons)}')
    print('note_ons')
    [print(i) for i in note_ons]
    print('')
    print('adjusted_note_ons')
    [print(i) for i in adjusted_note_ons]
    print('')
    print('BEGIN NOTE OFFS')
    print('')"""
    # ------------------------------------------------------

    # Same for note-offs
    note_offs = np.array([note.end for instrument in midi_data.instruments
                            for note in instrument.notes])
    adjusted_note_offs = np.interp(note_offs, original_times, new_times)

    # ------------------------------------------------------
    """print(f'note_offs: {len(note_offs)}')
    print(f'adjusted_note_offs: {len(adjusted_note_offs)}')
    print('note_offs')
    [print(i) for i in note_offs]
    print('')
    print('adjusted_note_offs')
    [print(i) for i in adjusted_note_offs]
    print('')"""
    # ------------------------------------------------------

    # Correct notes
    for n, note in enumerate([note for instrument in midi_data.instruments
                                for note in instrument.notes]):
        note.start = (adjusted_note_ons[n] > 0)*adjusted_note_ons[n]
        note.end = (adjusted_note_offs[n] > 0)*adjusted_note_offs[n]
        print(f'start: {note.start}')
        print(f'end: {note.end}')
        # Checking if the interval of the notes are correct and fixing them if not
        if note.end - note.start != interval[n]:
            note.end = note.start + interval[n]
            print(f'adjusted start: {note.start}')
            print(f'adjusted end: {note.end}')
            print('')
    print('')

    # final check
    """for instrument in midi_data.instruments:
        for note in instrument.notes:
            print(note)
        print(f'final notes: {len(instrument.notes)}')"""

    midi_data.write(output_path)

## Indian

In [9]:
url_list_i = list(channel_table['AllVideos'][0])
url_list_is = sample(url_list_i, 10)
url_list_is

['https://www.youtube.com/watch?v=1SCEk5o5N2Y',
 'https://www.youtube.com/watch?v=cE-_QdycJeQ',
 'https://www.youtube.com/watch?v=Getk5ZiF_A4',
 'https://www.youtube.com/watch?v=W9T1gISgct0',
 'https://www.youtube.com/watch?v=Ih7TdgOho6A',
 'https://www.youtube.com/watch?v=WxkFhZfnU4g',
 'https://www.youtube.com/watch?v=pNAi6WqePlM',
 'https://www.youtube.com/watch?v=Og-hxDhoYGc',
 'https://www.youtube.com/watch?v=JxKlo4PYvxI',
 'https://www.youtube.com/watch?v=P3l7v2a3haA']

In [ ]:
download('indian_2', url_list_is)

### Editing MT3 Transcriptions

In [25]:
genre = 'indian'
directory = os.path.join('dataset', 'mt3_inference', f'{genre}_mt3')
for root, dirs, files in os.walk(directory, topdown = False):
    for f in files:
        print(f'file: {f}')
        name, ext = f.split('.')
        if ext == 'mid':
            midi_path = os.path.join(root, f)
            output_path = os.path.join(root, f'{name}_TRIMMED.mid')
            print(f'midi_path: {midi_path}')
            print(f'output_path: {output_path}')
            remove_silence(midi_path, output_path)

file: Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover_mt3.mid
midi_path: dataset/mt3_inference/indian_mt3/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover_mt3.mid
output_path: dataset/mt3_inference/indian_mt3/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover_mt3_TRIMMED.mid
original midi: [Instrument(program=0, is_drum=False, name="")]
program: 0
new midi: [Instrument(program=0, is_drum=False, name="")]
Has notes!
[1.15909091 1.15909091 1.15909091 1.15909091 1.35       1.54090909
 1.72954545 2.09090909 2.27954545 2.45909091]
[0.         0.         0.         0.         0.19090909 0.38181818
 0.57045455 0.93181818 1.12045455 1.3       ]
file: Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | 

### Editing Ground Truths

In [143]:
genre = 'indian'
directory = os.path.join('dataset', 'ground_truth', f'{genre}_gt')
for root, dirs, files in os.walk(directory, topdown = False):
    print(root)
    for f in files:
        print(f'file: {f}')
        if f.startswith('.'):
            continue
        name, ext = f.split('.')
        midi_path = os.path.join(root, f)
        merged_path = os.path.join(root, f'{name}_MERGED.mid')
        print(f'midi_path: {midi_path}')
        print(f'merged_path: {merged_path}')
        merge_tracks(midi_path, merged_path)
        # complex_remove_silence(merged_path, output_path)

dataset/ground_truth/indian_gt
file: Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover.mid
midi_path: dataset/ground_truth/indian_gt/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover.mid
merged_path: dataset/ground_truth/indian_gt/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover_MERGED.mid
output_path: dataset/ground_truth/indian_gt/Sab Tera Piano Tutorial Instrumental Armaan Malik | Karaoke | Ringtone | Notes | Cover_TRIMMED.mid
original length of track: 815
leftover after removing: []
new length of track: 815
checking onsets: [5.62500000e-02 6.09375000e-02 6.09375000e-02 7.03125000e-02
 2.39062500e-01 4.35937500e-01 6.23437500e-01 9.84375000e-01
 1.18125000e+00 1.36875000e+00 1.74843750e+00 1.95000000e+00
 2.14218750e+00 3.22500000e+00 3.22968750e+00 3.23437500e+00
 3.24375000e+00 3.41718750e+00 3.59531250e+00 3.77812500e+00
 4.14843750e+00 4.33593750e+00 4.53281250e+00 4.9

## Hip-Hop

In [48]:
url_list_h = list(channel_table['AllVideos'][1])
url_list_hs = sample(url_list_h, 30)
url_list_hs

['https://www.youtube.com/watch?v=oB8BAUPUzL8',
 'https://www.youtube.com/watch?v=UtUTLHf08UQ',
 'https://www.youtube.com/watch?v=bCjNlVW9TEc',
 'https://www.youtube.com/watch?v=Grb8LpMwops',
 'https://www.youtube.com/watch?v=kYEWF8Z9BHY',
 'https://www.youtube.com/watch?v=ZTsNrrduEgg',
 'https://www.youtube.com/watch?v=6kGvTj1-eQk',
 'https://www.youtube.com/watch?v=JwLdrKRWGIg',
 'https://www.youtube.com/watch?v=1YoFtCWwnSU',
 'https://www.youtube.com/watch?v=k6BM-geg6nY',
 'https://www.youtube.com/watch?v=_SztZQUJYf4',
 'https://www.youtube.com/watch?v=85t3yl2P86M',
 'https://www.youtube.com/watch?v=RMPVvpawFaE',
 'https://www.youtube.com/watch?v=l8IpaKz_big',
 'https://www.youtube.com/watch?v=T5Batq7aikw',
 'https://www.youtube.com/watch?v=HTwmo7EPIQ4',
 'https://www.youtube.com/watch?v=SrMvWPomHpM',
 'https://www.youtube.com/watch?v=zV0Vw18feRw',
 'https://www.youtube.com/watch?v=vX_erEW5J88',
 'https://www.youtube.com/watch?v=51BSrt9SVfs',
 'https://www.youtube.com/watch?v=rpUXUk

In [ ]:
download('hip-hop', url_list_hs)

### Editing MT3 Transcriptions

In [92]:
genre = 'hip-hop'
directory = os.path.join('dataset', 'mt3_inference', f'{genre}_mt3')
for root, dirs, files in os.walk(directory, topdown = False):
    for f in files:
        print(f'file: {f}')
        name, ext = f.split('.')
        if ext == 'mid':
            midi_path = os.path.join(root, f)
            output_path = os.path.join(root, f'{name}_TRIMMED.mid')
            print(f'midi_path: {midi_path}')
            print(f'output_path: {output_path}')
            remove_silence(midi_path, output_path)

file: Drake - God's Plan (The Theorist Piano Cover).mp3
file: Drake - God's Plan (The Theorist Piano Cover)_mt3.mid
midi_path: dataset/mt3_inference/hip-hop_mt3/Drake - God's Plan (The Theorist Piano Cover)/Drake - God's Plan (The Theorist Piano Cover)_mt3.mid
output_path: dataset/mt3_inference/hip-hop_mt3/Drake - God's Plan (The Theorist Piano Cover)/Drake - God's Plan (The Theorist Piano Cover)_mt3_TRIMMED.mid
original midi: [Instrument(program=0, is_drum=False, name=""), Instrument(program=26, is_drum=False, name=""), Instrument(program=4, is_drum=False, name="")]
program: 0
new midi: [Instrument(program=0, is_drum=False, name="")]
Has notes!
[0.40909091 0.40909091 0.40909091 0.40909091 0.40909091 0.40909091
 0.40909091 0.40909091 0.82954545 0.82954545]
[0.         0.         0.         0.         0.         0.
 0.         0.         0.42045455 0.42045455]
file: Travis Scott - Highest In The Room (The Theorist Piano Cover).mp3
file: Travis Scott - Highest In The Room (The Theorist P

### Editing Ground Truths

In [159]:
genre = 'hip_hop'
directory = os.path.join('dataset', 'ground_truth', f'{genre}_gt')
for root, dirs, files in os.walk(directory, topdown = False):
    print(root)
    for f in files:
        print(f'file: {f}')
        if f.startswith('.'):
            continue
        name, ext = f.split('.')
        midi_path = os.path.join(root, f)
        merged_path = os.path.join(root, f'{name}_MERGED.mid')
        print(f'midi_path: {midi_path}')
        print(f'merged_path: {merged_path}')
        merge_tracks(midi_path, merged_path)

dataset/ground_truth/hip_hop_gt
file: The Weeknd ft SZA - Pray For Me (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/hip_hop_gt/The Weeknd ft SZA - Pray For Me (The Theorist Piano Cover).mid
merged_path: dataset/ground_truth/hip_hop_gt/The Weeknd ft SZA - Pray For Me (The Theorist Piano Cover)_MERGED.mid
file: XXXTENTACION - SAD! (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/hip_hop_gt/XXXTENTACION - SAD! (The Theorist Piano Cover).mid
merged_path: dataset/ground_truth/hip_hop_gt/XXXTENTACION - SAD! (The Theorist Piano Cover)_MERGED.mid
file: .DS_Store
file: XXXTENTACION - Jocelyn Flores (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/hip_hop_gt/XXXTENTACION - Jocelyn Flores (The Theorist Piano Cover).mid
merged_path: dataset/ground_truth/hip_hop_gt/XXXTENTACION - Jocelyn Flores (The Theorist Piano Cover)_MERGED.mid
file: Juice WRLD - Robbery (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/hip_hop_gt/Juice WRLD - Robbery (T

## R&B

### Editing MT3 Transcriptions

In [93]:
genre = 'r&b'
directory = os.path.join('dataset', 'mt3_inference', f'{genre}_mt3')
for root, dirs, files in os.walk(directory, topdown = False):
    for f in files:
        print(f'file: {f}')
        name, ext = f.split('.')
        if ext == 'mid':
            midi_path = os.path.join(root, f)
            output_path = os.path.join(root, f'{name}_TRIMMED.mid')
            print(f'midi_path: {midi_path}')
            print(f'output_path: {output_path}')
            remove_silence(midi_path, output_path)

file: Daniel Caesar - Get You (The Theorist Piano Cover)_mt3.mid
midi_path: dataset/mt3_inference/r&b_mt3/Daniel Caesar - Get You (The Theorist Piano Cover)/Daniel Caesar - Get You (The Theorist Piano Cover)_mt3.mid
output_path: dataset/mt3_inference/r&b_mt3/Daniel Caesar - Get You (The Theorist Piano Cover)/Daniel Caesar - Get You (The Theorist Piano Cover)_mt3_TRIMMED.mid
original midi: [Instrument(program=0, is_drum=False, name="")]
program: 0
new midi: [Instrument(program=0, is_drum=False, name="")]
Has notes!
[0.55       0.65       0.72045455 0.72045455 0.77045455 0.84090909
 0.90909091 0.90909091 3.27045455 3.27045455]
[0.         0.1        0.17045455 0.17045455 0.22045455 0.29090909
 0.35909091 0.35909091 2.72045455 2.72045455]
file: Daniel Caesar - Get You (The Theorist Piano Cover).mp3
file: Daniel Caesar - Blessed (The Theorist Piano Cover).mp3
file: Daniel Caesar - Blessed (The Theorist Piano Cover)_mt3.mid
midi_path: dataset/mt3_inference/r&b_mt3/Daniel Caesar - Blessed (T

### Editing Ground Truths

In [150]:
genre = 'r&b'
directory = os.path.join('dataset', 'ground_truth', f'{genre}_gt')
for root, dirs, files in os.walk(directory, topdown = False):
    print(root)
    for f in files:
        print(f'file: {f}')
        if f.startswith('.'):
            continue
        name, ext = f.split('.')
        midi_path = os.path.join(root, f)
        merged_path = os.path.join(root, f'{name}_MERGED.mid')
        print(f'midi_path: {midi_path}')
        print(f'merged_path: {merged_path}')
        merge_tracks(midi_path, merged_path)

dataset/ground_truth/r&b_gt
file: .DS_Store
file: Post Malone - Better Now (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/r&b_gt/Post Malone - Better Now (The Theorist Piano Cover).mid
merged_path: dataset/ground_truth/r&b_gt/Post Malone - Better Now (The Theorist Piano Cover)_MERGED.mid
file: Daniel Caesar - Japanese Denim (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/r&b_gt/Daniel Caesar - Japanese Denim (The Theorist Piano Cover).mid
merged_path: dataset/ground_truth/r&b_gt/Daniel Caesar - Japanese Denim (The Theorist Piano Cover)_MERGED.mid
file: Daniel Caesar - Get You (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/r&b_gt/Daniel Caesar - Get You (The Theorist Piano Cover).mid
merged_path: dataset/ground_truth/r&b_gt/Daniel Caesar - Get You (The Theorist Piano Cover)_MERGED.mid
file: The Weeknd - True Colors (The Theorist Piano Cover).mid
midi_path: dataset/ground_truth/r&b_gt/The Weeknd - True Colors (The Theorist Piano Cover).mid
m

## Electronic

In [ ]:
p = pytube.Playlist('https://www.youtube.com/watch?v=J1dnVrPizWo&list=PLh5yQEh2F60v3bjv5M1PlD-DO9V1D7GkI')
p.video_urls

In [53]:
url_list_e = list(p.video_urls)
url_list_es = sample(url_list_e, 30)
url_list_es

['https://www.youtube.com/watch?v=KEjPtSmWo1s',
 'https://www.youtube.com/watch?v=dZ-yGi0H_ZQ',
 'https://www.youtube.com/watch?v=LLL6V7pHW7A',
 'https://www.youtube.com/watch?v=PO_K82gBCl0',
 'https://www.youtube.com/watch?v=ftcqtyflluU',
 'https://www.youtube.com/watch?v=wwTDJVGEbFE',
 'https://www.youtube.com/watch?v=XcTsIKk5TPQ',
 'https://www.youtube.com/watch?v=n6yMZJxZb5M',
 'https://www.youtube.com/watch?v=kCh9s-y-gq4',
 'https://www.youtube.com/watch?v=Jvs3WMFX5aQ',
 'https://www.youtube.com/watch?v=v572eUdPz1c',
 'https://www.youtube.com/watch?v=_CNRSVbEM_Q',
 'https://www.youtube.com/watch?v=ATmkMmYHQB0',
 'https://www.youtube.com/watch?v=FoyJCHOrDZE',
 'https://www.youtube.com/watch?v=HQozceVazhI',
 'https://www.youtube.com/watch?v=as_PoRk6cwA',
 'https://www.youtube.com/watch?v=ZJwIrL2zXq0',
 'https://www.youtube.com/watch?v=QszzqPeyzRg',
 'https://www.youtube.com/watch?v=Kv5id4jI9qM',
 'https://www.youtube.com/watch?v=iTEgNS0T9C8',
 'https://www.youtube.com/watch?v=1eeROH

In [ ]:
download('electronic', url_list_es)

### Editing MT3 Transcriptions

In [ ]:
genre = 'electronic'
directory = os.path.join('dataset', 'mt3_inference', f'{genre}_mt3')
for root, dirs, files in os.walk(directory, topdown = False):
    for f in files:
        print(f'file: {f}')
        name, ext = f.split('.')
        if ext == 'mid':
            midi_path = os.path.join(root, f)
            output_path = os.path.join(root, f'{name}_TRIMMED.mid')
            print(f'midi_path: {midi_path}')
            print(f'output_path: {output_path}')
            remove_silence(midi_path, output_path)

### Editing Ground Truths

In [133]:
genre = 'electronic'
directory = os.path.join('dataset', 'ground_truth', f'{genre}_gt')
for root, dirs, files in os.walk(directory, topdown = False):
    print(root)
    for f in files:
        print(f'file: {f}')
        if f.startswith('.'):
            continue
        name, ext = f.split('.')
        midi_path = os.path.join(root, f)
        merged_path = os.path.join(root, f'{name}_MERGED.mid')
        output_path = os.path.join(root, f'{name}_TRIMMED.mid')
        print(f'midi_path: {midi_path}')
        print(f'merged_path: {merged_path}')
        print(f'output_path: {output_path}')
        merge_tracks(midi_path, merged_path)
        complex_remove_silence(merged_path, output_path)

dataset/ground_truth/electronic_gt
file: Noisestorm - Crab Rave Piano Cover + [MIDI].mid
midi_path: dataset/ground_truth/electronic_gt/Noisestorm - Crab Rave Piano Cover + [MIDI].mid
merged_path: dataset/ground_truth/electronic_gt/Noisestorm - Crab Rave Piano Cover + [MIDI]_MERGED.mid
output_path: dataset/ground_truth/electronic_gt/Noisestorm - Crab Rave Piano Cover + [MIDI]_TRIMMED.mid
original length of track: 2335
leftover after removing: []
new length of track: 2335
checking onsets: [  0.22395833   2.19791667   3.94791667 ... 192.94791667 193.07291667
 193.32291667]
original_times: 704
new_times: 704

start: 0.0
end: 0.22916666666666669
start: 1.9739583333333333
end: 2.2291666666666665
adjusted start: 1.9739583333333333
adjusted end: 2.229166666666667

start: 3.723958333333333
end: 3.9791666666666665
start: 3.9739583333333326
end: 4.229166666666667
adjusted start: 3.9739583333333326
adjusted end: 4.229166666666666

start: 5.973958333333333
end: 6.229166666666667
start: 7.7239583333

## Movie

In [56]:
p = pytube.Playlist('https://www.youtube.com/watch?v=b-jcsjozkD0&list=PLh5yQEh2F60uqmOl9oRWD6SyEarU2kqo2')
p.video_urls

['https://www.youtube.com/watch?v=b-jcsjozkD0', 'https://www.youtube.com/watch?v=rYlQxF4ud4A', 'https://www.youtube.com/watch?v=Po2xOfz_Cpw', 'https://www.youtube.com/watch?v=EEY0FsLDxPU', 'https://www.youtube.com/watch?v=vDD8mCv9wvg', 'https://www.youtube.com/watch?v=YZGphK9Bl3Y', 'https://www.youtube.com/watch?v=RpZiE21Vu5I', 'https://www.youtube.com/watch?v=sNKc_xrROUI', 'https://www.youtube.com/watch?v=0W7r6Jz5L0I', 'https://www.youtube.com/watch?v=q-CaI6oJKF4', 'https://www.youtube.com/watch?v=xBu3xWP6VUM', 'https://www.youtube.com/watch?v=ZTkTMeXJgaA', 'https://www.youtube.com/watch?v=vjf8iOpEn18', 'https://www.youtube.com/watch?v=5B6SPPk_Ipo', 'https://www.youtube.com/watch?v=lAK0IHbasnM', 'https://www.youtube.com/watch?v=PNbFSAH2nJ4', 'https://www.youtube.com/watch?v=HQZbeC2sf7E', 'https://www.youtube.com/watch?v=E4J8Zj6zM-k', 'https://www.youtube.com/watch?v=IMfP8ubbJzk', 'https://www.youtube.com/watch?v=ikTAmoEMWcs', 'https://www.youtube.com/watch?v=5FveSzkCQQc', 'https://www

In [59]:
url_list_m = list(p.video_urls)
url_list_ms = sample(url_list_m, 30)
url_list_ms

['https://www.youtube.com/watch?v=57SdNVHYdNk',
 'https://www.youtube.com/watch?v=VvdjHjBNFSM',
 'https://www.youtube.com/watch?v=lAK0IHbasnM',
 'https://www.youtube.com/watch?v=b-jcsjozkD0',
 'https://www.youtube.com/watch?v=vjf8iOpEn18',
 'https://www.youtube.com/watch?v=PNbFSAH2nJ4',
 'https://www.youtube.com/watch?v=0Pbz22SCpkw',
 'https://www.youtube.com/watch?v=ESyg_KQEKfY',
 'https://www.youtube.com/watch?v=MTG1Nt-un_0',
 'https://www.youtube.com/watch?v=NyoZJFCkA2I',
 'https://www.youtube.com/watch?v=hVNEkZzp8qg',
 'https://www.youtube.com/watch?v=QSHdFOBpEP4',
 'https://www.youtube.com/watch?v=tkFq0OGN5eY',
 'https://www.youtube.com/watch?v=YZGphK9Bl3Y',
 'https://www.youtube.com/watch?v=yblZO-g8KSA',
 'https://www.youtube.com/watch?v=D7L6QyStMl4',
 'https://www.youtube.com/watch?v=1Covpr48yDw',
 'https://www.youtube.com/watch?v=ikTAmoEMWcs',
 'https://www.youtube.com/watch?v=_riKsapJw9E',
 'https://www.youtube.com/watch?v=IMfP8ubbJzk',
 'https://www.youtube.com/watch?v=2nQJAN

### Editing MT3 Transcriptions

In [33]:
genre = 'movie'
directory = os.path.join('dataset', 'mt3_inference', f'{genre}_mt3')
for root, dirs, files in os.walk(directory, topdown = False):
    for f in files:
        print(f'file: {f}')
        name, ext = f.split('.')
        if ext == 'mid':
            midi_path = os.path.join(root, f)
            output_path = os.path.join(root, f'{name}_TRIMMED.mid')
            print(f'midi_path: {midi_path}')
            print(f'output_path: {output_path}')
            remove_silence(midi_path, output_path)

file: Sigrid - Everybody Knows [Justice League OST] Piano Cover + [MIDI].mp3
file: Sigrid - Everybody Knows [Justice League OST] Piano Cover + [MIDI]_mt3.mid
midi_path: dataset/mt3_inference/movie_mt3/Sigrid - Everybody Knows [Justice League OST] Piano Cover + [MIDI]/Sigrid - Everybody Knows [Justice League OST] Piano Cover + [MIDI]_mt3.mid
output_path: dataset/mt3_inference/movie_mt3/Sigrid - Everybody Knows [Justice League OST] Piano Cover + [MIDI]/Sigrid - Everybody Knows [Justice League OST] Piano Cover + [MIDI]_mt3_TRIMMED.mid
original midi: [Instrument(program=0, is_drum=False, name="")]
program: 0
new midi: [Instrument(program=0, is_drum=False, name="")]
Has notes!
[ 7.24090909  7.67954545  8.05        8.4         8.77045455  9.12954545
  9.49090909  9.8        10.12954545 10.47954545]
[0.         0.43863636 0.80909091 1.15909091 1.52954545 1.88863636
 2.25       2.55909091 2.88863636 3.23863636]
file: Hans Zimmer - Interstellar - Main Theme Piano Cover [FREE MIDI]_mt3.mid
midi_

### Editing Ground Truths

In [141]:
genre = 'movie'
directory = os.path.join('dataset', 'ground_truth', f'{genre}_gt')
for root, dirs, files in os.walk(directory, topdown = False):
    print(root)
    for f in files:
        print(f'file: {f}')
        if f.startswith('.'):
            continue
        name, ext = f.split('.')
        midi_path = os.path.join(root, f)
        merged_path = os.path.join(root, f'{name}_MERGED.mid')
        output_path = os.path.join(root, f'{name}_TRIMMED.mid')
        print(f'midi_path: {midi_path}')
        print(f'merged_path: {merged_path}')
        print(f'output_path: {output_path}')
        merge_tracks(midi_path, merged_path)
        complex_remove_silence(merged_path, output_path)

dataset/ground_truth/movie_gt
file: Hans Zimmer - Man of Steel Piano Cover [SHEET+MIDI].mid
midi_path: dataset/ground_truth/movie_gt/Hans Zimmer - Man of Steel Piano Cover [SHEET+MIDI].mid
merged_path: dataset/ground_truth/movie_gt/Hans Zimmer - Man of Steel Piano Cover [SHEET+MIDI]_MERGED.mid
output_path: dataset/ground_truth/movie_gt/Hans Zimmer - Man of Steel Piano Cover [SHEET+MIDI]_TRIMMED.mid
original length of track: 2795
index: 0
index: 2793
leftover after removing: [[Note(start=0.000000, end=1.875000, pitch=60, velocity=81)], [Note(start=260.000000, end=261.875000, pitch=60, velocity=81)]]
new length of track: 2793
checking onsets: [ 10.     11.     12.    ... 243.125 245.    245.   ]
original_times: 1599
new_times: 1599

start: 0.0
end: 0.875
start: 1.0
end: 1.875
start: 2.0
end: 2.875
start: 3.0
end: 3.875
start: 3.75
end: 3.979166666666666
start: 4.0
end: 4.875
start: 5.0
end: 5.875
start: 4.0
end: 6.84375
start: 6.0
end: 6.875
start: 4.0
end: 7.791666666666664
start: 7.0
e

## Trimming

In [19]:
# trial

midi_data = pretty_midi.PrettyMIDI('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/mt3_inference/indian_mt3/A Tribute To KK - Pyaar Ke Pal Piano Tutorial Instrumental Cover KK/A Tribute To KK - Pyaar Ke Pal Piano Tutorial Instrumental Cover KK_mt3.mid')
# original times
ori_times = midi_data.get_onsets()
print(ori_times[:10])
# new times
new_times = midi_data.get_onsets() - midi_data.get_onsets()[0]
print(new_times[:10])

# adjusting times
midi_data.adjust_times(ori_times, new_times)
print(midi_data.get_onsets())

midi_data.write('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/mt3_inference/indian_mt3/A Tribute To KK - Pyaar Ke Pal Piano Tutorial Instrumental Cover KK/A Tribute To KK - Pyaar Ke Pal Piano Tutorial Instrumental Cover KK_mt3_TRIMMED.mid')

[4.82954545 4.87954545 4.94090909 4.95       5.45909091 5.97045455
 6.45       8.07045455 8.3        8.57045455]
[0.         0.05       0.11136364 0.12045455 0.62954545 1.14090909
 1.62045455 3.24090909 3.47045455 3.74090909]
[0.00000000e+00 5.00000000e-02 1.11363636e-01 1.20454545e-01
 6.29545455e-01 1.14090909e+00 1.62045455e+00 3.24090909e+00
 3.47045455e+00 3.74090909e+00 4.22954545e+00 4.25000000e+00
 4.25000000e+00 4.72045455e+00 4.72954545e+00 4.96136364e+00
 5.19090909e+00 5.22045455e+00 5.71136364e+00 8.34090909e+00
 8.36136364e+00 8.82045455e+00 9.32045455e+00 9.81136364e+00
 1.14613636e+01 1.19500000e+01 1.21909091e+01 1.24295455e+01
 1.24295455e+01 1.29000000e+01 1.29000000e+01 1.31295455e+01
 1.33795455e+01 1.33795455e+01 1.38795455e+01 1.65795455e+01
 1.65795455e+01 1.70409091e+01 1.70409091e+01 1.72909091e+01
 1.75204545e+01 1.80113636e+01 1.95909091e+01 2.00795455e+01
 2.03000000e+01 2.05500000e+01 2.05500000e+01 2.05500000e+01
 2.10295455e+01 2.10613636e+01 2.12704545e

In [ ]:
# Load the MIDI file
midi_data = pretty_midi.PrettyMIDI('example.mid')

# Create a list of instruments to keep
keep_instruments = []
for instrument in midi_data.instruments:
    if instrument.is_drum or instrument.program in range(0, 8):
        # If the instrument is a drum or a piano-type instrument, add it to the list of instruments to keep
        keep_instruments.append(instrument)

# Remove all instruments that are not in the list of instruments to keep
midi_data.instruments = keep_instruments

# Write the modified MIDI file to disk
# midi_data.write('example_piano_only.mid')

In [77]:
midi_data = pretty_midi.PrettyMIDI('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/Alan Walker - Darkside feat AuRa and Tomine Harket Piano Cover + [MIDI].mid')
for instrument in midi_data.instruments:
    for note in instrument.notes:
        print(note)

Note(start=0.000000, end=0.250000, pitch=79, velocity=100)
Note(start=10.067708, end=10.848958, pitch=79, velocity=77)
Note(start=10.833333, end=11.093750, pitch=78, velocity=70)
Note(start=11.546875, end=11.984375, pitch=76, velocity=71)
Note(start=11.921875, end=12.302083, pitch=71, velocity=57)
Note(start=11.536458, end=12.562500, pitch=64, velocity=53)
Note(start=12.286458, end=12.630208, pitch=76, velocity=57)
Note(start=12.614583, end=12.802083, pitch=71, velocity=53)
Note(start=12.947917, end=13.385417, pitch=62, velocity=57)
Note(start=13.286458, end=13.437500, pitch=66, velocity=55)
Note(start=13.625000, end=13.958333, pitch=83, velocity=71)
Note(start=13.968750, end=14.046875, pitch=78, velocity=70)
Note(start=14.364583, end=14.786458, pitch=76, velocity=67)
Note(start=14.750000, end=15.072917, pitch=67, velocity=60)
Note(start=15.109375, end=15.442708, pitch=72, velocity=60)
Note(start=14.364583, end=15.484375, pitch=60, velocity=55)
Note(start=15.458333, end=15.546875, pitc

In [53]:
midi_data = pretty_midi.PrettyMIDI('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/Alan Walker - Darkside feat AuRa and Tomine Harket Piano Cover + [MIDI].mid')
new_instrument = pretty_midi.Instrument(program=0, is_drum=False, name="merged")
for instrument in midi_data.instruments:
    # print(f'original notes: {instrument.notes}')
    notes_lst = instrument.notes
    for note in instrument.notes:
        print(note)
    print(len(notes_lst))
    leftover = []
    i = 0

    while i < len(instrument.notes) - 1:
        diff = instrument.notes[i+1].start - instrument.notes[i].end

        if diff >= 3:
            if i + 1 == len(instrument.notes) - 1:
                leftover.append(instrument.notes[i + 1])
                notes_lst.remove(instrument.notes[i + 1])
            else:
                leftover.append(instrument.notes[i])
                notes_lst.remove(instrument.notes[i])
        i += 1

# original (after "trimming" gaps)
for note in notes_lst:
    new_instrument.notes.append(note)
midi_data.instruments = [new_instrument]
print(len(new_instrument.notes))
print(leftover)

# midi_data.write('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/poo_2.mid')

Note(start=0.000000, end=0.250000, pitch=79, velocity=100)
Note(start=10.067708, end=10.848958, pitch=79, velocity=77)
Note(start=10.833333, end=11.093750, pitch=78, velocity=70)
Note(start=11.546875, end=11.984375, pitch=76, velocity=71)
Note(start=11.921875, end=12.302083, pitch=71, velocity=57)
Note(start=11.536458, end=12.562500, pitch=64, velocity=53)
Note(start=12.286458, end=12.630208, pitch=76, velocity=57)
Note(start=12.614583, end=12.802083, pitch=71, velocity=53)
Note(start=12.947917, end=13.385417, pitch=62, velocity=57)
Note(start=13.286458, end=13.437500, pitch=66, velocity=55)
Note(start=13.625000, end=13.958333, pitch=83, velocity=71)
Note(start=13.968750, end=14.046875, pitch=78, velocity=70)
Note(start=14.364583, end=14.786458, pitch=76, velocity=67)
Note(start=14.750000, end=15.072917, pitch=67, velocity=60)
Note(start=15.109375, end=15.442708, pitch=72, velocity=60)
Note(start=14.364583, end=15.484375, pitch=60, velocity=55)
Note(start=15.458333, end=15.546875, pitc

In [36]:
midi_data = pretty_midi.PrettyMIDI('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/Avicii - Levels Melodic Piano Cover + [MIDI].mid')
for instrument in midi_data.instruments:
    print(instrument)
    for note in instrument.notes:
        print(note)

Instrument(program=0, is_drum=False, name="Steinway Grand Piano")
Note(start=0.252930, end=0.544922, pitch=83, velocity=61)
Note(start=0.632812, end=0.809570, pitch=81, velocity=51)
Note(start=0.773438, end=0.924805, pitch=78, velocity=64)
Note(start=0.930664, end=1.075195, pitch=81, velocity=62)
Note(start=0.273438, end=1.242188, pitch=71, velocity=49)
Note(start=1.250000, end=1.500977, pitch=81, velocity=50)
Note(start=1.449219, end=1.567383, pitch=78, velocity=48)
Note(start=1.768555, end=2.139648, pitch=74, velocity=43)
Note(start=2.273438, end=2.365234, pitch=74, velocity=46)
Note(start=2.722656, end=2.834961, pitch=73, velocity=62)
Note(start=2.975586, end=3.042969, pitch=73, velocity=75)
Note(start=0.291992, end=3.730469, pitch=66, velocity=61)
Note(start=0.235352, end=4.725586, pitch=59, velocity=44)
Note(start=5.397461, end=5.570312, pitch=66, velocity=57)
Note(start=5.339844, end=5.585938, pitch=62, velocity=51)
Note(start=5.517578, end=5.789062, pitch=71, velocity=71)
Note(s

In [39]:
midi_data = pretty_midi.PrettyMIDI('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/Alan Walker - Force Piano Cover + [MIDI].mid')
for instrument in midi_data.instruments:
    print(instrument)
    for note in instrument.notes:
        print(note)

Instrument(program=0, is_drum=False, name="Kontakt 5 #2")
Note(start=8.000000, end=8.250000, pitch=85, velocity=67)
Note(start=9.000000, end=9.250000, pitch=83, velocity=68)
Note(start=9.500000, end=9.750000, pitch=81, velocity=68)
Note(start=10.000000, end=10.250000, pitch=80, velocity=69)
Note(start=11.000000, end=11.250000, pitch=76, velocity=70)
Note(start=11.500000, end=11.750000, pitch=78, velocity=71)
Note(start=12.000000, end=12.250000, pitch=80, velocity=71)
Note(start=13.000000, end=13.250000, pitch=81, velocity=72)
Note(start=13.500000, end=13.750000, pitch=80, velocity=73)
Note(start=14.000000, end=14.250000, pitch=78, velocity=73)
Note(start=15.000000, end=15.250000, pitch=76, velocity=75)
Note(start=15.500000, end=15.750000, pitch=75, velocity=75)
Note(start=16.000000, end=16.250000, pitch=85, velocity=76)
Note(start=17.000000, end=17.250000, pitch=83, velocity=77)
Note(start=17.500000, end=17.750000, pitch=81, velocity=77)
Note(start=18.000000, end=18.250000, pitch=80, v

In [70]:
midi_data = pretty_midi.PrettyMIDI('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/Alan Walker - THE DRUM Piano Cover [FREE MIDI].mid')
new_instrument = pretty_midi.Instrument(program=0, is_drum=False, name="new")
for instrument in midi_data.instruments:
    print(instrument)
    for note in instrument.notes:
        print(note)
        new_instrument.notes.append(note)
midi_data.instruments = [new_instrument]
midi_data.write('/Users/huongngo/Desktop/PERSONAL PROJECTS/gehirn/evaluation/dataset/ground_truth/electronic_gt/poo.mid')

Instrument(program=0, is_drum=False, name="CFX Concert Grand")
Note(start=0.000000, end=0.250000, pitch=75, velocity=80)
Note(start=0.250000, end=0.500000, pitch=77, velocity=83)
Note(start=0.500000, end=0.750000, pitch=78, velocity=86)
Note(start=0.750000, end=1.000000, pitch=80, velocity=87)
Note(start=1.000000, end=1.500000, pitch=82, velocity=87)
Note(start=1.500000, end=1.750000, pitch=82, velocity=86)
Note(start=1.750000, end=2.000000, pitch=78, velocity=84)
Note(start=2.000000, end=2.500000, pitch=83, velocity=84)
Note(start=2.500000, end=2.750000, pitch=83, velocity=85)
Note(start=2.750000, end=3.000000, pitch=82, velocity=85)
Note(start=3.000000, end=3.500000, pitch=80, velocity=84)
Note(start=3.500000, end=4.000000, pitch=78, velocity=84)
Note(start=4.000000, end=8.000000, pitch=77, velocity=76)
Note(start=8.000000, end=8.250000, pitch=75, velocity=75)
Note(start=8.250000, end=8.500000, pitch=78, velocity=77)
Note(start=8.500000, end=8.750000, pitch=78, velocity=78)
Note(star

In [168]:
genres = ['electronic', 'movie', 'hip-hop', 'r&b', 'indian', 'anime', 'k-pop', 'video_games']
for genre in genres:
  directory = os.path.join('dataset/final_eval', genre)
  print(f'genre directory: {directory}')
  for root, dirs, files in os.walk(directory, topdown = False):
    # directory in genre directory
    for d in dirs:
        print(d)
        gt_merged = os.path.join(root, f'{d}_MERGED')
        gt_trimmed = os.path.join(root, f'{d}_TRIMMED')
        mt3_clean = os.path.join(root, f'{d}_mt3_TRIMMED')
        # w/ trimmed
        precision, recall, f1_score = eval(gt_trimmed, mt3_clean)
        # w/ merged
        precision, recall, f1_score = eval(gt_merged, mt3_clean)

genre directory: dataset/final_eval/electronic
Avicii - Dear Boy Piano Cover [SHEET+MIDI]
David Guetta ft Sia - Titanium Piano Cover + [MIDI]
Avicii - Levels Melodic Piano Cover + [MIDI]
Alan Walker - THE DRUM Piano Cover [FREE MIDI]
K-391 - Summertime Piano Cover [SHEET + MIDI]
Avicii - Wake Me Up Piano Cover + [MIDI]
Defqwop - Heart Afire (feat Strix) Piano Cover [SHEET+MIDI]
Avicii Best Melodies Piano Cover Pt 2 + [MIDI]
Martin Garrix & Dua Lipa - Scared To Be Lonely Piano Cover + [MIDI]
Elektronomia - Sky High Piano Cover + [MIDI]
AXEL F Piano Cover [SHEET+MIDI]
Nadia Ali - Rapture Avicii Remix Piano Cover + [MIDI]
Avicii - I Could Be The One Piano Cover + [MIDI]
Alan Walker - Darkside feat AuRa and Tomine Harket Piano Cover + [MIDI]
Alan Walker - Faded Piano Cover + [MIDI]
Noisestorm - Crab Rave Piano Cover + [MIDI]
IMAGINE DRAGONS - ENEMY Piano Cover with Beat [FREE MIDI]
Alan Walker & ISÁK - Sorry Piano Cover + [MIDI]
Alan Walker - Force Piano Cover + [MIDI]
Avicii - Sunset Jes

In [ ]:
f_eval = {'name': [], 'genre': [], 'precision': [], 'recall': [], 'f1': [], 'merged': []}
genres = ['electronic', 'movie', 'hip-hop', 'r&b', 'indian', 'anime', 'k-pop', 'video_games']
file_invalid = []
for genre in genres:
  directory = os.path.join('/content/final_eval/final_eval', genre)
  # print(f'genre directory: {directory}')
  print(f'genre: {genre}')
  prec = []
  rec = []
  f1 = []
  prec_m = []
  rec_m = []
  f1_m = []
  # going through each genre
  for root, dirs, files in os.walk(directory, topdown = False):
    # directory in genre directory
    for d in dirs:
        f_eval['name'].append(d)
        f_eval['genre'].append(genre)
        # print(d)
        gt_merged = os.path.join(root, d, f'{d}_MERGED.mid')
        gt_trimmed = os.path.join(root, d, f'{d}_TRIMMED.mid')
        mt3_clean = os.path.join(root, d, f'{d}_mt3_TRIMMED.mid')

        if os.path.exists(gt_merged) == False or os.path.exists(gt_trimmed) == False or os.path.exists(mt3_clean) == False:
            file_invalid.append(d)
            continue

        precision, recall, f1_score = eval(gt_trimmed, mt3_clean)
        print(f'trimmed - precision: {precision}, recall: {recall}, f1_score: {f1_score}')

        if genre == 'electronic' or genre == 'movie':
          # w/ trimmed
            precision, recall, f1_score = eval(gt_trimmed, mt3_clean)
            print(f'trimmed - precision: {precision}, recall: {recall}, f1_score: {f1_score}')
          
            # w/ merged
            precision_m, recall_m, f1_score_m = eval(gt_merged, mt3_clean)

            prec_m.append(precision_m)
            rec_m.append(recall_m)
            f1_m.append(f1_score_m)

            f_eval['precision'].append(precision)
            f_eval['recall'].append(recall)
            f_eval['f1'].append(f1_score)
            f_eval['merged'].append(1)

            print(f'merged - precision: {precision_m}, recall: {recall_m}, f1_score: {f1_score_m}')

        if genre == 'hip-hop' or genre == 'r&b' or genre == 'indian':
            precision, recall, f1_score = eval(gt_merged, mt3_clean)
            print(f'precision: {precision}, recall: {recall}, f1_score: {f1_score}')

        if genre == 'anime' or genre == 'k-pop' or genre == 'video_games':
            mt3_clean = os.path.join(root, f'{d}_mt3_trimmed.mid')
            gt = os.path.join(root, f'{d}_gt.mid')
            precision, recall, f1_score = eval(gt, mt3_clean)
            print(f'precision: {precision}, recall: {recall}, f1_score: {f1_score}')

        # score for each song
        f_eval['precision'].append(precision)
        f_eval['recall'].append(recall)
        f_eval['f1'].append(f1_score)
        f_eval['merged'].append(0)
        
        prec.append(precision)
        rec.append(recall)
        f1.append(f1_score)
        
    avg_prec = np.mean(prec)
    avg_rec = np.mean(rec)
    avg_f1 = np.mean(f1)
    if genre == 'electronic' or genre == 'movie':
        avg_prec_m = np.mean(prec_m)
        avg_rec_m = np.mean(rec_m)
        avg_f1_m = np.mean(f1_m)
print(f'average precision: {avg_prec}')
print(f'average recall: {avg_rec}')
print(f'average f1: {avg_f1}')

In [193]:
import multiprocessing
from typing import List, Union, Any
import pytube
GENRE_TAG = 'electronic'

In [194]:
def robust_download(video_url: str) -> List[Union[str, int]]:
    """Downloads the mp4 video file from the input YouTube video URL, converts it to an mp3 audio file and returns
       the video metadata.

    Args:
        video_url: The URL of the YouTube video to download.

    Returns:
        A tuple of two items:
            - A dictionary containing video metadata, including video ID, file path, length, rating, description, and keywords.
            - A list containing video channel ID, video ID, description, length, publish date, and file path.
    """
    try:
        video = pytube.YouTube(video_url)
        video_name = video.title.replace('/', '') + '.mp4'
        audio_name = video.title.replace('/', '') + '.mp3'
        output_path = os.path.join('dataset', GENRE_TAG, video.title)

        if not os.path.isdir(output_path) and not video.length > 360:
            os.makedirs(output_path)

        if not os.path.isfile(os.path.join(output_path, audio_name)) and not video.length > 360:
            video.streams.filter(progressive=True, file_extension='mp4').order_by('resolution').asc() \
                 .first().download(filename=video_name, output_path=output_path)

            video_editor = moviepy.editor.VideoFileClip(os.path.join(output_path, video_name))
            video_editor.audio.write_audiofile(os.path.join(output_path, audio_name), logger=None)
            os.remove(os.path.join(output_path, video_name))

        row = []
        if not video.length > 360:
            row = [video.video_id, video.channel_id,
                   video.title, video.description,
                   video.length, video.publish_date,
                   video.rating, video.keywords,
                   os.path.join(output_path, audio_name)
            ]

        return row

    except (PytubeError, http.client.IncompleteRead) as e:
        print('Error: ', e)
        return []

In [197]:
def song_playlists(playlist_id: str) -> pd.DataFrame:
    
    data = []
    url = f'https://www.youtube.com/playlist?list={playlist_id}'
    playlist = pytube.Playlist(url)
    video_urls = playlist.video_urls
    with multiprocessing.Pool(8) as pool:
        for row in pool.map(robust_download, video_urls):
            row.insert(2, playlist_id)
            data.append(row)

    videos_table = pd.DataFrame(data, columns=[
        'VideoID', 'ChannelID', 'PlaylistID',
        'videoTitle', 'descriptions', 'length', 'publishedDate',
        'videoRating', 'videoKeyWords', 'pathToRaw']
    )
    output_path = os.path.join('data_mining', 'dataset', GENRE_TAG, 'META_DATA.csv')
    videos_table.to_csv(output_path)
    return videos_table

In [191]:
song_playlists('PLEb0_nNrLidAcRNKYubWmueQKGbhp9cUf')

Error:  Exception while accessing title of https://youtube.com/watch?v=-4tjVEn-uSE. Please file a bug report at https://github.com/pytube/pytube
Error:  Exception while accessing title of https://youtube.com/watch?v=DU8clJVUWWg. Please file a bug report at https://github.com/pytube/pytube
Error:  Exception while accessing title of https://youtube.com/watch?v=sLyrooXOGkU. Please file a bug report at https://github.com/pytube/pytube
Error:  Exception while accessing title of https://youtube.com/watch?v=M9MqgOSRUdI. Please file a bug report at https://github.com/pytube/pytube
Error:  Exception while accessing title of https://youtube.com/watch?v=xP5KGsMC7Xc. Please file a bug report at https://github.com/pytube/pytube
Error:  Exception while accessing title of https://youtube.com/watch?v=zwk8AHI_Gcg. Please file a bug report at https://github.com/pytube/pytube
Error:  Exception while accessing title of https://youtube.com/watch?v=aGFP92nHVcs. Please file a bug report at https://github.com

OSError: Cannot save file into a non-existent directory: 'dataset/video_games'